Simulation

In [1]:
import sys
sys.path.insert(0, "\\Users\\Gebruiker\\Documents\\GitHub\\parcels\\")  # Set path to find the newest parcels code

from parcels import FieldSet, ParticleSet, Variable, JITParticle, ScipyParticle, AdvectionRK4_3D, ErrorCode, plotTrajectoriesFile
import numpy as np
from operator import attrgetter
from datetime import timedelta
from netCDF4 import Dataset,num2date,date2num
from explfunctions import deleteparticle, removeNaNs, FinalDistance

Now we are going to obtain flowfields in netcdf form. Because the general 2D structure in Parcels expects lon-lat, while these flowfield are 1D and depth, we are going to transform the data, add a dimension and use from_data to read in the 3D flow fields. This also sets up further research in 3D. Here we decide which flow we are going to analyse and whether to do it forwards or backwards in time

In [2]:
filename = 'output-corals-regridded-parabolic-wave'
fb = 'forward' #variable to determine whether the flowfields are analysed 'forward' or 'backward' in time
corald = Dataset(filename+'.nc','r+') # read netcdf file with input

# Extract all variables into np arrays --> in the future xarray will be used
T = corald.variables['T'][:]
X = corald.variables['X'][:]
Y = corald.variables['Y'][:]
U = corald.variables['U'][:]
V = corald.variables['V'][:]

corald.close()

Here the variables are going to be changed to fit parcels

In [3]:
U = np.asarray(U)
U = np.expand_dims(U,2)            # add a third dimension

V = np.asarray(V)
V = np.expand_dims(V,2)            # add a third dimension

t = num2date(T,units='seconds since 2000-01-01 00:00:00.0') # make t a datetime object
t = date2num(t,units='seconds since 2000-01-01 00:00:00.0')

times = t
xs = X
ys = np.asarray([-1,0,1])          # third dimension with length 3. 2D flow field will be inserted on the middle value to ensure the AdvectionRK4_3D works correctly
depths = -Y                        # Y was height, but parcels expects depth

u = np.zeros(U.shape)
u = np.concatenate((u,u,u),axis=2) # add the third dimension
u[:,:,1,:] = U[:,:,0,:]            # add the data to the middle value of the third dimension
v = np.zeros(u.shape)
w = np.zeros(U.shape)
w = np.concatenate((w,w,w),axis=2) # add the third dimension
w[:,:,1,:] = -V[:,:,0,:]           # because depth = -Y, w = -V
dist = np.zeros(u.shape)
coralmap = np.load('coralmap.npy')
dist[:,:,1,:] = np.asarray([coralmap]*len(u))
closest = np.zeros(u.shape)
closestobject = np.load('closestobject.npy')
# index = np.ma.masked_array(closestobject,umask.mask)
closest[:,:,1,:] = np.asarray([closestobject]*len(u))

Now we are going to read the data into a parcels fieldset using FieldSet.from_data.

In [4]:
data = {'U': u,
        'V': v,
        'W': w,
        'D': dist,
        'C': closest}
dimensions = {'lon':xs,
              'lat':ys,
              'depth':depths,
              'time':times}
fieldset = FieldSet.from_data(data=data, dimensions= dimensions, mesh='flat')

fieldset.C.interp_method = 'nearest'

In [5]:
class DistParticle(JITParticle):  # Define a new particle class that contains three extra variables
    finaldistance = Variable('finaldistance', initial=0., dtype=np.float32)  # the distance travelled
    prevlon = Variable('prevlon', dtype=np.float32, to_write=False,
                        initial=attrgetter('lon'))  # the previous longitude
    prevlat = Variable('prevlat', dtype=np.float32, to_write=False,
                        initial=attrgetter('lat'))  # the previous latitude.
    prevdepth = Variable('prevdepth', dtype=np.float32, to_write=False,
                        initial=attrgetter('depth'))  # the previous latitude.
    d2c = Variable('d2c', dtype=np.float32, initial=0.)
    closestobject = Variable('closestobject', dtype=np.float32, initial=0.)
    
def SampleD(particle, fieldset, time):  # Custom function that samples fieldset.D and fieldset.C at particle location
    particle.d2c = fieldset.D[time, particle.depth, particle.lat, particle.lon]
    particle.closestobject = fieldset.C[time, particle.depth, particle.lat, particle.lon]

Now that the data are read into a fieldset object, we want to define the attributes of the particles we are going to release as a particleset object. In this experiment, we want to release particles at all gridpoints in the model, except for the ones where coral geometrical objects are in the flow. Also, we want to define for how long the particles are advected, which timestep to use and what output to obtain.

In [6]:
lons, ds = np.meshgrid(xs,depths)                        # meshgrid at all gridpoints in the flow data
um = np.ma.masked_invalid(u[0,:,1,:])                    # retrieve mask from flowfield to take out points over coral objects

lons = np.ma.masked_array(lons,mask=um.mask)             # mask points in meshgrid
lons = lons.flatten()
ds = np.ma.masked_array(ds,mask=um.mask)                 # mask points in meshgrid
ds = ds.flatten()

outputdt = timedelta(seconds=0.1)                        # timesteps to create output at
dt=timedelta(seconds=0.01)                               # timesteps to calculate particle trajectories
runtime=timedelta(seconds=10)                            # total time to execute the particleset
lats = np.asarray([0]*len(lons))                         # all particles must start and stay on the middle value of the extra dimension
inittime = np.asarray([0]*len(lons))                     # default time to start the particles is zero
if fb == 'backward':                                     # change timestep and start time when in 'backward' mode
    dt = dt*-1
    inittime = np.asarray([runtime.seconds]*len(lons))

In [7]:
pset = ParticleSet(fieldset=fieldset, pclass=DistParticle, lon=lons, lat=lats, depth=ds,time=inittime)

The masked values at the coral objects are seen by parcels as zero, so we are going to remove these trajectories. If we do not do this we are calculating many more trajectories which all start at the same time at lon = 0 and depth = 0. The function that does this is removeNaNs in the explfunctions file.

In [8]:
k_removeNaNs = pset.Kernel(removeNaNs)
k_sample = pset.Kernel(SampleD)    # Casting the SampleP function to a kernel.

pset.execute(k_removeNaNs+k_sample, runtime = timedelta(seconds=0))

INFO: Compiled DistParticleremoveNaNsSampleD ==> C:\Users\GEBRUI~1\AppData\Local\Temp\parcels-tmp\311ec82583be84b96cc19dcf54df1a5a_0.dll


Aside from the trajectories, we would like to find out which particles are beached, i.e. find themselves on the coral where there are no velocities to advect them. To look at this through time, we have written the function FinalDistance, which saves the distance moved in the last timestep at each output time. If this is zero, we assume the particle to be stuck. The output file is named based on the input file, whether the run is forward or backward in time and the runtime.

In [9]:
k_dist = pset.Kernel(FinalDistance)  # Casting the FinalDistance function to a kernel.
# k_adv = pset.Kernel(AdvectionRK4_3D_v)  # Casting the advection function with velocities to a kernel.

pset.execute(AdvectionRK4_3D+k_dist+k_sample,
             runtime=runtime,
             dt=dt,
             recovery = {ErrorCode.ErrorOutOfBounds:deleteparticle},
             output_file=pset.ParticleFile(name=filename+fb+str(runtime.seconds), outputdt=outputdt)
            )

INFO: Compiled DistParticleAdvectionRK4_3DFinalDistanceSampleD ==> C:\Users\GEBRUI~1\AppData\Local\Temp\parcels-tmp\892b291a62a8a24b23dbb0d3fa8dfe31_0.dll


Particle 448 has died at t = 0.05999999865889549 at lon, lat, depth = 3.988322, 0.0, -0.49
Particle 449 has died at t = 0.0 at lon, lat, depth = 3.99, 0.0, -0.49
Particle 450 has died at t = 0.0 at lon, lat, depth = 4.0, 0.0, -0.49
Particle 523 has died at t = 0.06999999843537807 at lon, lat, depth = 4.738735, 0.0, -0.49
Particle 524 has died at t = 0.0 at lon, lat, depth = 4.74, 0.0, -0.49
Particle 525 has died at t = 0.0 at lon, lat, depth = 4.75, 0.0, -0.49
Particle 526 has died at t = 0.06999999843537807 at lon, lat, depth = 4.768771, 0.0, -0.49
Particle 527 has died at t = 0.0 at lon, lat, depth = 4.77, 0.0, -0.49
Particle 528 has died at t = 0.0 at lon, lat, depth = 4.78, 0.0, -0.49
Particle 529 has died at t = 0.0 at lon, lat, depth = 4.79, 0.0, -0.49
Particle 530 has died at t = 0.0 at lon, lat, depth = 4.8, 0.0, -0.49
Particle 531 has died at t = 0.0 at lon, lat, depth = 4.81, 0.0, -0.49
Particle 532 has died at t = 0.0 at lon, lat, depth = 4.82, 0.0, -0.49
Particle 533 has di

INFO: Temporary output files are stored in out-XMSJPMBU.
INFO: You can use "parcels_convert_npydir_to_netcdf out-XMSJPMBU" to convert these to a NetCDF file during the run.
N/A% (0 of 10.0) |                       | Elapsed Time: 0:00:00 ETA:  --:--:--


Particle 435 has died at t = 0.3899999912828207 at lon, lat, depth = 3.9854088, 0.0, -0.49
Particle 436 has died at t = 0.3799999915063381 at lon, lat, depth = 3.9897234, 0.0, -0.49
Particle 437 has died at t = 0.35999999195337296 at lon, lat, depth = 3.9884238, 0.0, -0.49
Particle 438 has died at t = 0.3399999924004078 at lon, lat, depth = 3.9876213, 0.0, -0.49
Particle 439 has died at t = 0.3199999928474426 at lon, lat, depth = 3.9873176, 0.0, -0.49
Particle 440 has died at t = 0.29999999329447746 at lon, lat, depth = 3.9874933, 0.0, -0.49
Particle 509 has died at t = 0.3899999912828207 at lon, lat, depth = 4.734677, 0.0, -0.49
Particle 510 has died at t = 0.3799999915063381 at lon, lat, depth = 4.738193, 0.0, -0.49
Particle 511 has died at t = 0.35999999195337296 at lon, lat, depth = 4.7354116, 0.0, -0.49
Particle 512 has died at t = 0.3499999921768904 at lon, lat, depth = 4.739348, 0.0, -0.49
Particle 513 has died at t = 0.3299999926239252 at lon, lat, depth = 4.737481, 0.0, -0.49


  4% (0.4 of 10.0) |                     | Elapsed Time: 0:00:04 ETA:   0:01:40


...

 97% (9.799999999999981 of 10.0) |###### | Elapsed Time: 0:03:00 ETA:   0:00:01


Particle 36753 has died at t = 9.889999778941274 at lon, lat, depth = 8.489764, 0.0, -0.14026137
Particle 42154 has died at t = 9.809999780729413 at lon, lat, depth = 8.468165, 0.0, -0.15621772
Particle 46649 has died at t = 9.79999978095293 at lon, lat, depth = 8.485371, 0.0, -0.15295501
Particle 60660 has died at t = 9.819999780505896 at lon, lat, depth = 8.464058, 0.0, -0.2256983
Particle 62451 has died at t = 9.809999780729413 at lon, lat, depth = 8.459247, 0.0, -0.22883305
Particle 63751 has died at t = 9.859999779611826 at lon, lat, depth = 8.484647, 0.0, -0.14534391
Particle 65209 has died at t = 9.79999978095293 at lon, lat, depth = 8.477672, 0.0, -0.17224108
Particle 67839 has died at t = 9.829999780282378 at lon, lat, depth = 8.459968, 0.0, -0.22537553
Particle 67911 has died at t = 9.819999780505896 at lon, lat, depth = 8.469076, 0.0, -0.23505284
Particle 68723 has died at t = 9.83999978005886 at lon, lat, depth = 8.463974, 0.0, -0.21669467
Particle 68736 has died at t = 9.8

 98% (9.89999999999998 of 10.0) |####### | Elapsed Time: 0:03:01 ETA:   0:00:00


Particle 23266 has died at t = 9.9899997767061 at lon, lat, depth = 8.4693575, 0.0, -0.13240132
Particle 23267 has died at t = 9.969999777153134 at lon, lat, depth = 8.489825, 0.0, -0.13105135
Particle 34806 has died at t = 9.929999778047204 at lon, lat, depth = 8.475487, 0.0, -0.16904421
Particle 34812 has died at t = 9.979999776929617 at lon, lat, depth = 8.485142, 0.0, -0.16405399
Particle 35705 has died at t = 9.959999777376652 at lon, lat, depth = 8.488397, 0.0, -0.16398321
Particle 35707 has died at t = 9.919999778270721 at lon, lat, depth = 8.487154, 0.0, -0.16296574
Particle 44625 has died at t = 9.919999778270721 at lon, lat, depth = 8.470267, 0.0, -0.16789643
Particle 48364 has died at t = 9.929999778047204 at lon, lat, depth = 8.477317, 0.0, -0.16954693
Particle 52653 has died at t = 9.939999777823687 at lon, lat, depth = 8.478989, 0.0, -0.17030826
Particle 60059 has died at t = 9.919999778270721 at lon, lat, depth = 8.472555, 0.0, -0.16799645
Particle 63402 has died at t = 

 99% (9.99999999999998 of 10.0) |####### | Elapsed Time: 0:03:02 ETA:   0:00:00
100% (10.0 of 10.0) |####################| Elapsed Time: 0:03:02 Time:  0:03:02


Now that the particle trajectories have been simulated, we arrive at the analysis part of the exploration. We open the output file and the file which contains the flow fields again. We want to be able to open any output file so we are going to define again which run, how many seconds and whether it is forwards or backwards in time 